In [1]:
print("bruh")

bruh


In [1]:
import ib_gate
from datetime import datetime
if __name__ == "__main__":
    import sys
    # port number socker server is using (paper: 7497, live: 7496)
    # PORT_NUMBER = sys.argv[1]
    app = ib_gate.main(port=7497)

ruinnn
serverVersion:151 connectionTime:b'20200827 15:34:26 EST'


ERROR -1 2104 Market data farm connection is OK:cafarm
ERROR -1 2104 Market data farm connection is OK:hfarm
ERROR -1 2104 Market data farm connection is OK:cashfarm


In [5]:
a = app.get_price_history( symbols=['TSLA'], start_date=datetime(2020,8,1), end_date=datetime(2020,8,24),
                  bar_size="5 mins", rth=True)
display(a)
# os.chdir('C:\\S\\stocks')
try:a.to_csv("csv/tsla.csv")
except Exception as e: print(e)



TSLA                                      
                    open_price     high      low close_price  volume
2020-08-03 09:30:00    1450.64  1460.83  1444.38     1456.39  2203.0
2020-08-03 09:35:00    1456.99  1464.00  1455.32     1459.83  1388.0
2020-08-03 09:40:00    1460.02  1476.38  1459.67     1476.25  1821.0
2020-08-03 09:45:00    1476.51  1478.76  1460.50     1464.54  1454.0
2020-08-03 09:50:00    1464.53  1474.09  1464.30     1469.29  1064.0
...                        ...      ...      ...         ...     ...
2020-08-21 15:35:00    2056.12  2064.47  2046.13     2054.10  3054.0
2020-08-21 15:40:00    2054.32  2056.47  2036.00     2041.71  3454.0
2020-08-21 15:45:00    2042.00  2054.00  2041.10     2046.30  2191.0
2020-08-21 15:50:00    2045.72  2057.92  2042.09     2055.67  2376.0
2020-08-21 15:55:00    2056.19  2056.19  2046.65     2050.00  2373.0

[1170 rows x 5 columns]

In [8]:
### TEST NORMAL 
pd.set_option("display.max_rows", None, "display.max_columns", None)

import plotly.graph_objects as go
from plotly.subplots import make_subplots

import matplotlib.pyplot as plt
from pandas.plotting import register_matplotlib_converters
register_matplotlib_converters()
plt.rcParams["figure.figsize"] = [15, 10]

b=a.copy()
b.columns=b.columns.droplevel()
# display(b)
def setMA(df,p_swma=10,p_lwma=20,p_signal=3,p_rsi=36):
    exp1 = df.close_price.ewm(span=p_swma, adjust=False).mean()
    exp2 = df.close_price.ewm(span=p_lwma, adjust=False).mean()
    df['close_ch'] = df.close_price.diff(1)
    df['swma'] = exp1
    df['lwma'] = exp2
    df['macd'] = exp1-exp2
    df['macd_ch'] = df.macd.diff(1)
    df['signal'] = b.macd.ewm(span=p_signal, adjust=False).mean()
    df['signal_ch'] = df.signal.diff(1)
    df['conv']=df.macd_ch-df.signal_ch
    df['conv_ch']=df.macd_ch-df.signal_ch
    
    close = df['close_price']
    delta = close.diff() 
    up, down = delta.copy(), delta.copy()
    up[up < 0] = 0
    down[down > 0] = 0
    roll_up = up.ewm(com=p_rsi - 1, adjust=False).mean()
    roll_down = down.ewm(com=p_rsi - 1, adjust=False).mean().abs()
    rs = roll_up / roll_down   # relative strength =  average gain/average loss
    rsi = 100-(100/(1+rs))
    df['rsi'] = rsi
    
    return df[p_lwma-1:]

df = setMA(b)
# display(df)
fig = make_subplots(rows=3, cols=1, 
                    shared_xaxes=True, 
                    vertical_spacing=0.02)
candlesticks = go.Candlestick(x=df.index,
                open=df['open_price'],
                high=df['high'],
                low=df['low'],
                close=df['close_price'])
swma = go.Scatter(x=df.index, y=df.swma, line=dict(color='orange', width=1))
lwma = go.Scatter(x=df.index, y=df.lwma, line=dict(color='green', width=1))

macd = go.Scatter(x=df.index, y=df.macd, line=dict(color='blue', width=1),yaxis="y2")
signal = go.Scatter(x=df.index, y=df.signal, line=dict(color='red', width=2),yaxis="y2")

rsi = go.Scatter(x=df.index, y=df.rsi, line=dict(color='gray', width=2),yaxis="y3")

data = [candlesticks,swma,lwma,macd,signal,rsi]

layout = go.Layout( yaxis=dict(
        domain=[.33, 1]
    ),
    legend=dict(
        traceorder="reversed"
    ),
    yaxis2=dict(
        domain=[.2, .33]
    ),
    yaxis3=dict(
    domain=[0, .2]
    ),
)

fig = go.Figure(data=data,layout=layout)
fig.show()

stats = {
        'state':0,
    
        'open':0,
        'close':0,
        'profit':0,
        'pos':0,
    
        'signal':0,
        'signalp':0,
    
        'cross':-1
}
def momentumState(macd,signal,price,rsi):
    stats['signalp']=stats['signal']
    if signal>=macd:stats['signal']=1 
    else:stats['signal']=-1
    
    
    if stats['signal'] != stats['signalp']:
        
        stats['cross']= stats['cross']+1
        stats['state']= stats['signal']
        if stats['cross']<=0: stats['state']=0
        else: 
            stats['state'] = stats['signal']
            if stats['open'] == 0:
                print(f"OPEN {stats['signal']}:"+str(price))
                stats['open']=price
            else:
                stats['close'] = price
                stats['pos']+=1
                if stats['signalp']==1:
                    stats['profit']+=(stats['close']-stats['open'])
#                     print((stats['close']-stats['open']))
                    print("CLOSE :"+str(price)+f" | PROFIT: {(stats['close']-stats['open'])}")
                    stats['open'],stats['close'] = price,0
                    print(f"OPEN {stats['signal']}:"+str(price))
                if stats['signalp']==-1:
                    stats['profit']+=(stats['open']-stats['close'])
                    print("CLOSE :"+str(price)+f" | PROFIT: {(stats['open']-stats['close'])}")
#                     print((stats['open']-stats['close']))
                    stats['open'],stats['close'] = price,0
                    print(f"OPEN {stats['signal']}:"+str(price))
        
#     print(stats['signalp'],stats['signal'],stats['cross'])
    return stats['state']
df['state'] = df.apply(lambda x: momentumState(x.macd, x.signal,x.close_price,x.rsi),1)
print(stats['profit']*15,stats['pos'])
display(df)



OPEN 1:1481.05
CLOSE :1481.3 | PROFIT: 0.25
OPEN -1:1481.3
CLOSE :1481.86 | PROFIT: -0.5599999999999454
OPEN 1:1481.86
CLOSE :1482.06 | PROFIT: 0.20000000000004547
OPEN -1:1482.06
CLOSE :1482.7 | PROFIT: -0.6400000000001
OPEN 1:1482.7
CLOSE :1481.39 | PROFIT: -1.3099999999999454
OPEN -1:1481.39
CLOSE :1480.0 | PROFIT: 1.3900000000001
OPEN 1:1480.0
CLOSE :1480.65 | PROFIT: 0.650000000000091
OPEN -1:1480.65
CLOSE :1479.42 | PROFIT: 1.2300000000000182
OPEN 1:1479.42
CLOSE :1480.88 | PROFIT: 1.4600000000000364
OPEN -1:1480.88
CLOSE :1479.47 | PROFIT: 1.4100000000000819
OPEN 1:1479.47
CLOSE :1480.04 | PROFIT: 0.5699999999999363
OPEN -1:1480.04
CLOSE :1478.28 | PROFIT: 1.759999999999991
OPEN 1:1478.28
CLOSE :1479.28 | PROFIT: 1.0
OPEN -1:1479.28
CLOSE :1479.86 | PROFIT: -0.5799999999999272
OPEN 1:1479.86
CLOSE :1480.31 | PROFIT: 0.4500000000000455
OPEN -1:1480.31
CLOSE :1480.95 | PROFIT: -0.6400000000001
OPEN 1:1480.95
CLOSE :1482.4 | PROFIT: 1.4500000000000455
OPEN -1:1482.4
CLOSE :1482.2 |

C:\Users\mysli\AppData\Local\Continuum\anaconda3\envs\webauto\lib\site-packages\ipykernel_launcher.py:125: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



open_price     high      low  close_price  volume  \
2020-08-05 12:03:10     1480.58  1480.99  1480.58      1480.99     5.0   
2020-08-05 12:03:20     1480.99  1480.99  1480.98      1480.99     0.0   
2020-08-05 12:03:30     1480.95  1480.96  1480.95      1480.95     1.0   
2020-08-05 12:03:40     1481.05  1481.05  1481.04      1481.05     1.0   
2020-08-05 12:03:50     1481.05  1481.05  1481.04      1481.05     0.0   
2020-08-05 12:04:00     1481.05  1481.05  1481.04      1481.05     0.0   
2020-08-05 12:04:10     1481.05  1481.05  1481.04      1481.05     0.0   
2020-08-05 12:04:20     1480.60  1481.00  1480.60      1481.00     4.0   
2020-08-05 12:04:30     1481.00  1481.00  1480.99      1481.00     0.0   
2020-08-05 12:04:40     1481.07  1481.07  1480.99      1481.00    24.0   
2020-08-05 12:04:50     1481.46  1481.46  1480.99      1481.00     2.0   
2020-08-05 12:05:00     1481.00  1481.00  1480.99      1481.00     2.0   
2020-08-05 12:05:10     1481.25  1481.31  1481.25      1481.30     3.0   
2020-08-05 12:05:20     1481.48  1482.00  1481.30      1482.00    11.0   
2020-08-05 12:05:30     1482.49  1482.96  1482.49      1482.51    14.0   
2020-08-05 12:05:40     1482.51  1482.51  1482.51      1482.51     0.0   
2020-08-05 12:05:50     1482.53  1482.54  1482.53      1482.53     1.0   
2020-08-05 12:06:00     1482.36  1482.37  1481.86      1481.86     9.0   
2020-08-05 12:06:10     1481.86  1481.86  1481.86      1481.86     0.0   
2020-08-05 12:06:20     1481.86  1481.86  1481.86      1481.86     0.0   
2020-08-05 12:06:30     1481.86  1481.86  1481.86      1481.86     0.0   
2020-08-05 12:06:40     1480.00  1481.66  1480.00      1481.66     4.0   
2020-08-05 12:06:50     1481.66  1481.66  1481.65      1481.66     0.0   
2020-08-05 12:07:00     1481.66  1481.66  1481.65      1481.66     0.0   
2020-08-05 12:07:10     1481.66  1481.66  1481.65      1481.66     0.0   
2020-08-05 12:07:20     1481.05  1481.06  1481.05      1481.05     1.0   
2020-08-05 12:07:30     1481.48  1482.07  1481.47      1482.06     3.0   
2020-08-05 12:07:40     1482.06  1482.07  1482.06      1482.06     0.0   
2020-08-05 12:07:50     1482.67  1483.01  1482.66      1483.00    19.0   
2020-08-05 12:08:00     1483.15  1483.26  1483.14      1483.26     3.0   
2020-08-05 12:08:10     1483.26  1483.26  1483.26      1483.26     0.0   
2020-08-05 12:08:20     1483.57  1483.98  1483.49      1483.69     9.0   
2020-08-05 12:08:30     1483.69  1483.69  1483.68      1483.69     0.0   
2020-08-05 12:08:40     1483.50  1483.59  1483.47      1483.48    17.0   
2020-08-05 12:08:50     1483.25  1483.25  1482.70      1482.70     4.0   
2020-08-05 12:09:00     1482.00  1482.00  1482.00      1482.00     1.0   
2020-08-05 12:09:10     1482.54  1482.64  1482.17      1482.18     8.0   
2020-08-05 12:09:20     1483.26  1484.00  1483.00      1483.38    15.0   
2020-08-05 12:09:30     1483.83  1483.83  1483.00      1483.01    14.0   
2020-08-05 12:09:40     1483.01  1483.01  1483.01      1483.01     0.0   
2020-08-05 12:09:50     1482.50  1482.50  1482.50      1482.50     1.0   
2020-08-05 12:10:00     1482.15  1482.15  1481.38      1481.57     7.0   
2020-08-05 12:10:10     1481.43  1481.43  1481.42      1481.43     7.0   
2020-08-05 12:10:20     1481.43  1481.43  1481.42      1481.43     0.0   
2020-08-05 12:10:30     1481.25  1481.25  1481.25      1481.25     1.0   
2020-08-05 12:10:40     1481.25  1481.25  1481.25      1481.25     0.0   
2020-08-05 12:10:50     1481.25  1481.25  1481.25      1481.25     0.0   
2020-08-05 12:11:00     1481.25  1481.25  1481.25      1481.25     0.0   
2020-08-05 12:11:10     1481.25  1481.25  1481.25      1481.25     0.0   
2020-08-05 12:11:20     1481.40  1481.41  1481.40      1481.40     1.0   
2020-08-05 12:11:30     1480.67  1480.67  1480.66      1480.67     1.0   
2020-08-05 12:11:40     1480.87  1481.47  1480.86      1481.02    17.0   
2020-08-05 12:11:50     1481.00  1481.39  1480.99      1481.39     9.0   
2020-08-05 12:12:00     1

In [13]:
### TEST NORMAL 
pd.set_option("display.max_rows", None, "display.max_columns", None)

import plotly.graph_objects as go
from plotly.subplots import make_subplots

import matplotlib.pyplot as plt
from pandas.plotting import register_matplotlib_converters
register_matplotlib_converters()
plt.rcParams["figure.figsize"] = [15, 10]

b=a.copy()
b.columns=b.columns.droplevel()

def setMA(df,p_swma=8,p_lwma=24,p_signal=6,p_rsi=36):
    exp1 = df.close_price.ewm(span=p_swma, adjust=False).mean()
    exp2 = df.close_price.ewm(span=p_lwma, adjust=False).mean()
    df['close_ch'] = df.close_price.diff(1)
    df['swma'] = exp1
    df['lwma'] = exp2
    df['macd'] = exp1-exp2
    df['macd_dir'] = ""
    df['macd_ch'] = df.macd.diff(1)
    df['signal'] = b.macd.ewm(span=p_signal, adjust=False).mean()
    df['signal_ch'] = df.signal.diff(2)/2
    df['conv']=df.macd_ch-df.signal_ch
    df['conv_ch']=df.macd_ch-df.signal_ch
    df['conv_ch_ewma']=df.conv_ch.ewm(span=4,adjust=False).mean()
    close = df['close_price']
    delta = close.diff() 
    up, down = delta.copy(), delta.copy()
    up[up < 0] = 0
    down[down > 0] = 0
    roll_up = up.ewm(com=p_rsi - 1, adjust=False).mean()
    roll_down = down.ewm(com=p_rsi - 1, adjust=False).mean().abs()
    rs = roll_up / roll_down   # relative strength =  average gain/average loss
    rsi = 100-(100/(1+rs))
    df['rsi'] = rsi
    
    return df[p_lwma-1:]

df = setMA(b)

fig = make_subplots(rows=3, cols=1, 
                    shared_xaxes=True, 
                    vertical_spacing=0.02)
candlesticks = go.Candlestick(x=df.index,
                open=df['open_price'],
                high=df['high'],
                low=df['low'],
                close=df['close_price'])
swma = go.Scatter(x=df.index, y=df.swma, line=dict(color='orange', width=1))
lwma = go.Scatter(x=df.index, y=df.lwma, line=dict(color='green', width=1))

macd = go.Scatter(x=df.index, y=df.macd, line=dict(color='blue', width=1),yaxis="y2")
signal = go.Scatter(x=df.index, y=df.signal, line=dict(color='red', width=2),yaxis="y2")

rsi = go.Scatter(x=df.index, y=df.rsi, line=dict(color='gray', width=2),yaxis="y3")

data = [candlesticks,swma,lwma,macd,signal,rsi]

layout = go.Layout( yaxis=dict(
        domain=[.33, 1]
    ),
    legend=dict(
        traceorder="reversed"
    ),
    yaxis2=dict(
        domain=[.2, .33]
    ),
    yaxis3=dict(
    domain=[0, .2]
    ),
)

fig = go.Figure(data=data,layout=layout)
fig.show()

stats = {
        'state':0,
    
        'open':0,
        'close':0,
        'profit':0,
        'pos':0,
    
        'signal':0,
        'signalp':0,
    
        'cross':-1
}
def momentumState(macd,signal,signal_ch,price,rsi):
    stats['signalp']=stats['signal']
    if signal>=macd:stats['signal']=-1 
    elif signal<macd:stats['signal']=1
    
    
    if stats['signal'] != stats['signalp']:
        stats['cross']= stats['cross']+1
        
    if stats['cross']<=0: stats['state']=0
    else: 
        if stats['state']==0 and stats['signal']==1 and signal>=0:
            stats['state'] = stats['signal']
            stats['open'] = price
        if stats['state'] == 1 and signal_ch <= 0:
            stats['close'] = price
            stats['state'] = 0
            print(stats['close']-stats['open'])
            stats['open'] = 0
        elif stats['signal']==-1 and signal <0:
            stats['state'] = stats['signal']
            stats['open'] = price
    return [stats['state'],"test"]
df['state'] = df.apply(lambda x: momentumState(x.macd, x.signal,x.signal_ch,x.close_price,x.rsi),1)
print(stats['profit']*15,stats['pos'])
display(df)



C:\Users\mysli\AppData\Local\Continuum\anaconda3\envs\webauto\lib\site-packages\ipykernel_launcher.py:115: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



0 0


open_price     high      low  close_price  volume  \
2020-08-03 12:03:50     1498.93  1498.94  1498.93      1498.93     1.0   
2020-08-03 12:04:00     1499.05  1499.05  1498.25      1498.25     8.0   
2020-08-03 12:04:10     1497.97  1497.98  1497.39      1497.39     5.0   
2020-08-03 12:04:20     1497.28  1497.48  1496.94      1497.48     5.0   
2020-08-03 12:04:30     1497.55  1497.55  1496.05      1497.17    39.0   
2020-08-03 12:04:40     1496.71  1497.02  1496.70      1497.02     2.0   
2020-08-03 12:04:50     1497.63  1497.63  1495.43      1496.27    38.0   
2020-08-03 12:05:00     1496.55  1496.55  1494.50      1494.50     6.0   
2020-08-03 12:05:10     1494.00  1495.01  1494.00      1494.35    18.0   
2020-08-03 12:05:20     1495.22  1495.23  1494.74      1495.16    24.0   
2020-08-03 12:05:30     1494.77  1494.86  1494.69      1494.85     5.0   
2020-08-03 12:05:40     1495.25  1495.52  1494.96      1495.52     8.0   
2020-08-03 12:05:50     1495.54  1496.24  1495.53      1496.13    15.0   
2020-08-03 12:06:00     1496.13  1496.13  1496.13      1496.13     0.0   
2020-08-03 12:06:10     1495.71  1497.82  1495.38      1497.81    27.0   
2020-08-03 12:06:20     1497.17  1497.65  1497.09      1497.65    23.0   
2020-08-03 12:06:30     1497.53  1497.53  1497.52      1497.53     3.0   
2020-08-03 12:06:40     1497.39  1497.40  1497.39      1497.39     6.0   
2020-08-03 12:06:50     1497.51  1497.79  1496.24      1496.24    25.0   
2020-08-03 12:07:00     1496.64  1496.65  1496.64      1496.64     1.0   
2020-08-03 12:07:10     1496.51  1496.51  1496.51      1496.51     1.0   
2020-08-03 12:07:20     1496.76  1496.76  1496.76      1496.76     1.0   
2020-08-03 12:07:30     1496.51  1496.51  1496.34      1496.34     2.0   
2020-08-03 12:07:40     1496.35  1496.60  1496.35      1496.59     3.0   
2020-08-03 12:07:50     1495.86  1495.86  1495.47      1495.48     4.0   
2020-08-03 12:08:00     1495.76  1496.00  1495.48      1496.00    24.0   
2020-08-03 12:08:10     1495.91  1495.92  1495.00      1495.00    12.0   
2020-08-03 12:08:20     1494.65  1496.62  1494.65      1496.61    22.0   
2020-08-03 12:08:30     1497.50  1497.79  1497.24      1497.79    13.0   
2020-08-03 12:08:40     1497.92  1497.92  1497.68      1497.68     7.0   
2020-08-03 12:08:50     1497.74  1498.99  1497.58      1498.38    21.0   
2020-08-03 12:09:00     1498.53  1498.53  1498.53      1498.53     1.0   
2020-08-03 12:09:10     1498.63  1499.55  1498.26      1498.85    19.0   
2020-08-03 12:09:20     1498.85  1498.86  1498.85      1498.85     0.0   
2020-08-03 12:09:30     1498.80  1499.34  1498.56      1498.56     7.0   
2020-08-03 12:09:40     1498.40  1498.59  1498.37      1498.37     7.0   
2020-08-03 12:09:50     1498.10  1498.77  1498.10      1498.77     2.0   
2020-08-03 12:10:00     1499.09  1499.09  1498.55      1498.66     9.0   
2020-08-03 12:10:10     1498.60  1498.60  1497.92      1497.92    12.0   
2020-08-03 12:10:20     1497.61  1497.61  1496.99      1497.09     6.0   
2020-08-03 12:10:30     1497.84  1497.85  1497.50      1497.50     7.0   
2020-08-03 12:10:40     1497.85  1497.90  1496.99      1496.99     8.0   
2020-08-03 12:10:50     1496.50  1496.50  1496.49      1496.50     1.0   
2020-08-03 12:11:00     1496.50  1496.50  1496.49      1496.50     0.0   
2020-08-03 12:11:10     1496.55  1496.88  1496.42      1496.88     6.0   
2020-08-03 12:11:20     1497.04  1497.37  1496.42      1497.37     7.0   
2020-08-03 12:11:30     1496.33  1496.33  1496.33      1496.33     1.0   
2020-08-03 12:11:40     1496.33  1496.33  1496.33      1496.33     0.0   
2020-08-03 12:11:50     1496.05  1496.31  1496.04      1496.30     2.0   
2020-08-03 12:12:00     1496.24  1497.59  1496.24      1497.24    16.0   
2020-08-03 12:12:10     1497.38  1497.38  1496.88      1496.88    16.0   
2020-08-03 12:12:20     1496.89  1497.44  1496.89      1497.15    16.0   
2020-08-03 12:12:30     1496.73  1496.73  1494.17      1494.67    16.0   
2020-08-03 12:12:40     1